In [1]:
import pandas as pd

In [2]:
df = pd.read_csv("../Jiggins_Zenodo_Img_Master.csv", low_memory=False)

In [3]:
df.nunique()

CAMID               12586
X                   49359
Image_name          37821
View                   10
zenodo_name            36
zenodo_link            32
Sequence            11301
Taxonomic_Name        363
Locality              645
Sample_accession     1571
Collected_by           12
Other_ID             3088
Date                  810
Dataset                 8
Store                 142
Brood                 226
Death_Date             82
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               6
file_type               3
dtype: int64

In [4]:
df.file_type.value_counts()

file_type
jpg    37072
raw    12226
tif       61
Name: count, dtype: int64

In [5]:
df.View.value_counts()

View
dorsal                15128
ventral               13424
Dorsal                 8360
Ventral                8090
ventral                1644
forewing dorsal         406
hindwing dorsal         406
forewing ventral        406
hindwing ventral        406
Dorsal and Ventral       18
Name: count, dtype: int64

Not great that `ventral` gets listed twice as lowercase and _again_ as `Ventral`.

### Standardize `View` Column
Let's standardize `View` so that there isn't a discrepancy based on case.

In [6]:
df["View"] = df.View.str.lower()
df.View.value_counts()

View
dorsal                23488
ventral               21514
ventral                1644
forewing dorsal         406
hindwing dorsal         406
forewing ventral        406
hindwing ventral        406
dorsal and ventral       18
Name: count, dtype: int64

In [7]:
print(df.View.unique())

['dorsal' 'ventral' nan 'dorsal and ventral' 'ventral ' 'forewing dorsal'
 'hindwing dorsal' 'forewing ventral' 'hindwing ventral']


Yes, one has a space after it, so we'll replace that.

In [8]:
df.loc[df["View"] == "ventral ", "View"] = "ventral"
df.View.value_counts() 

View
dorsal                23488
ventral               23158
forewing dorsal         406
hindwing dorsal         406
forewing ventral        406
hindwing ventral        406
dorsal and ventral       18
Name: count, dtype: int64

### Add Record Number Column
We'll add a `record_number` column for easier matching to the license/citation file.

In [9]:
def get_record_number(url):
    num = url.split(sep = "/")[-1]
    return num

In [10]:
df["record_number"] = df.zenodo_link.apply(get_record_number)
df.record_number.nunique()

32

We have 32 unique records represented in the full dataset. When we reduce down to just the Heliconius images, this will probably be less.

### Add `species` and `subspecies` Columns
This will make some analysis easier and allow for easy viewing on the [Data Dashboard](https://huggingface.co/spaces/imageomics/dashboard-prototype).

In [11]:
def get_species(taxa_name):
    if type(taxa_name) != float: #taxa name not null
        species = taxa_name.split(sep = " ssp")[0]
        return species
    else:
        return taxa_name

In [12]:
def get_subspecies(taxa_name):
    if type(taxa_name) != float:
        if "ssp." in taxa_name:
            subspecies = taxa_name.split(sep = "ssp. ")[1]
        elif "ssp " in taxa_name:
            subspecies = taxa_name.split(sep = "ssp ")[1]
        else:
            subspecies = None
    else:
        subspecies = None
    return subspecies

In [13]:
df["species"] = df.Taxonomic_Name.apply(get_species)
df.species.nunique()

246

In [14]:
df["subspecies"] = df.Taxonomic_Name.apply(get_subspecies)
df.subspecies.nunique()

139

Cross Types are labeled differently:
They are all abbreviations, we have `malleti (mal), plesseni (ple), notabilis (not), lativitta (lat)`, and Neil would guess that `latRo` refers to lativitta with a rounded apical band (e.g., a phenotypic variant of lativitta), but he couldn't say for sure without some more digging, so that will have to stay as-is. We will leave the `Test cross...` ones, but there is not much more to do with them.

In [15]:
df.Cross_Type.dropna().unique()

array(['mal', 'mal x ple', 'ple', 'ple x mal', 'latRo x not',
       '(latRo x not) x not', '(mal x ple) x mal', '(mal x ple) x ple',
       'ple x (mal x ple)', '(ple x mal) x (mal x ple)', 'lat x not',
       '(ple x mal) x ple', '(mal x ple) x (mal x ple)',
       '(ple x mal) x mal', '(ple x mal) x (ple x mal)',
       '(mal x ple) x (ple x mal)', 'hybrid', 'mal x (ple x mal)',
       '(lat x not) x lat', '(lat x not) x not', 'Ac heterozygote',
       'ple x (ple x mal)', '2 banded', 'lat',
       'Test cross (2 banded F2 x 2 banded F2)',
       'Test cross (4 spots x 2 banded)', 'Test cross (N heterozygozity)',
       'Test cross (short HW bar)', 'Test cross (4 spots x 4 spots)',
       'Test cross (N heterozygocity - NBNN x mal - thin)'], dtype=object)

In [16]:
def clean_cross_types(cross_type):
    if type(cross_type) != float:
        cross_type = cross_type.replace("mal", "malleti")
        cross_type = cross_type.replace("ple", "plesseni")
        cross_type = cross_type.replace("not", "notabilis")
        if "latRo" not in cross_type:
            #latRo does not cross with lativitta, so only apply when latRo isn't present
            cross_type = cross_type.replace("lat", "lativitta")
    return cross_type

In [17]:
df["Cross_Type"] = df["Cross_Type"].apply(clean_cross_types)

Now we can fill these cross types in for the `subspecies` column (all Cross Types are just labeled to the spceies level in `Taxonomic_Name`, so they did not get processed previously).

In [18]:
cross_type_subspecies = [ct for ct in list(df.Cross_Type.dropna().unique()) if "Test" not in ct and "banded" not in ct]
cross_type_subspecies.remove("hybrid")
cross_type_subspecies.remove("Ac heterozygote")

for ct in cross_type_subspecies:
    df.loc[df["Cross_Type"] == ct, "subspecies"] = ct

df.subspecies.nunique()


156

In [19]:
len(cross_type_subspecies)

21

In [20]:
df.loc[df["Cross_Type"].notna(), "subspecies"].value_counts()

subspecies
(malleti x plesseni) x malleti                 1204
plesseni x (malleti x plesseni)                 600
malleti x (plesseni x malleti)                  370
(plesseni x malleti) x plesseni                 363
(plesseni x malleti) x (malleti x plesseni)     354
(plesseni x malleti) x (plesseni x malleti)     286
(malleti x plesseni) x plesseni                 278
plesseni x malleti                              234
malleti x plesseni                              192
lativitta x notabilis                           136
(lativitta x notabilis) x lativitta             110
plesseni x (plesseni x malleti)                 106
(lativitta x notabilis) x notabilis             106
(malleti x plesseni) x (malleti x plesseni)      98
(plesseni x malleti) x malleti                   80
(malleti x plesseni) x (plesseni x malleti)      56
malleti                                          28
plesseni                                         28
(latRo x notabilis) x notabilis                  16
l

In [21]:
already_present_subspecies = []

for subspecies in list(df.loc[df["Cross_Type"].notna(), "subspecies"].dropna().unique()):
    if subspecies in list(df.loc[~df["Cross_Type"].notna(), "subspecies"].dropna().unique()):
        already_present_subspecies.append(subspecies)

print(len(already_present_subspecies))
already_present_subspecies

4


['malleti', 'plesseni', 'plesseni x malleti', 'lativitta']

Perfect, this adds 17 more subspecies (`lativitta`, `plessani`, `maletti`, and `plesseni x malleti` were already represented). Note, this is based on _exact_ duplicates. `notabilis x lativitta` is also already in the dataset, but the order (where the cross types are concerned) general goes `maternal x paternal`.

In [22]:
df.sample(7)

CAMID      X       Image_name     View  \
1986     19N1989  21369    19N1989_v.JPG  ventral   
45062  CAM044423  34391  CAM044423_d.CR2   dorsal   
48534        E23  37555        E23_d.CR2   dorsal   
45206  CAM044445  37132  CAM044445_d.JPG   dorsal   
12212  CAM010238  23307       10238v.jpg  ventral   
39059  CAM043418  30654  CAM043418_v.JPG  ventral   
38163  CAM043170  29755  CAM043170_d.CR2   dorsal   

                                          zenodo_name  \
1986               0.sheffield.ps.nn.ikiam.batch2.csv   
45062              batch2.Peru.image.names.Zenodo.csv   
48534              Anniina.Matilla.Field.Caught.E.csv   
45206              batch3.Peru.image.names.Zenodo.csv   
12212  Heliconius_wing_old_photos_2001_2019_part1.csv   
39059              batch1.Peru.image.names.Zenodo.csv   
38163              batch1.Peru.image.names.Zenodo.csv   

                             zenodo_link Sequence  \
1986   https://zenodo.org/record/4288311    1,989   
45062  https://zenodo.org/record/4287444   44,423   
48534  https://zenodo.org/record/2554218      NaN   
45206  https://zenodo.org/record/4288250   44,445   
12212  https://zenodo.org/record/2552371   10,238   
39059  https://zenodo.org/record/3569598   43,418   
38163  https://zenodo.org/record/3569598   43,170   

                          Taxonomic_Name           Locality Sample_accession  \
1986   Heliconius melpomene ssp. malleti  Ikiam Mariposario              NaN   
45062                 Taygetis cleopatra             B6old6              NaN   
48534                                NaN                NaN              NaN   
45206                 Taygetis cleopatra             B4old2              NaN   
12212                     Heliconius sp.                NaN              NaN   
39059           Archaeoprepona licomedes             B6rec6              NaN   
38163                  Adelpha mesentina             F3rec2              NaN   

       ...      Brood Death_Date Cross_Type Stage     Sex Unit_Type file_type  \
1986   ...  IKIAM.P44        NaN        NaN   NaN    Male    reared       jpg   
45062  ...        NaN        NaN        NaN   NaN     NaN       NaN       raw   
48534  ...        NaN        NaN        NaN   NaN     NaN       NaN       raw   
45206  ...        NaN        NaN        NaN   NaN     NaN       NaN       jpg   
12212  ...       B043        NaN        NaN   NaN  Female    reared       jpg   
39059  ...        NaN        NaN        NaN   NaN     NaN       NaN       jpg   
38163  ...        NaN        NaN        NaN   NaN     NaN       NaN       raw   

      record_number                   species subspecies  
1986        4288311      Heliconius melpomene    malleti  
45062       4287444        Taygetis cleopatra       None  
48534       2554218                       NaN       None  
45206       4288250        Taygetis cleopatra       None  
12212       2552371            Heliconius sp.       None  
39059       3569598  Archaeoprepona licomedes       None  
38163       3569598         Adelpha mesentina       None  

[7 rows x 25 columns]

### Add Genus Column

This willl allow us to easily remove all non Heliconius samples, and make some image stats easier to see.

In [23]:
def get_genus(species):
    if type(species) != float: #taxa name not null
        return species.split(sep = " ")[0]
    return species

In [24]:
df["genus"] = df["species"].apply(get_genus)
df.genus.nunique()

94

Final stats for all data summarized here.

In [25]:
df.nunique()

CAMID               12586
X                   49359
Image_name          37821
View                    7
zenodo_name            36
zenodo_link            32
Sequence            11301
Taxonomic_Name        363
Locality              645
Sample_accession     1571
Collected_by           12
Other_ID             3088
Date                  810
Dataset                 8
Store                 142
Brood                 226
Death_Date             82
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               6
file_type               3
record_number          32
species               246
subspecies            156
genus                  94
dtype: int64

In [26]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 49359 entries, 0 to 49358
Data columns (total 26 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             49359 non-null  object
 1   X                 49359 non-null  int64 
 2   Image_name        49359 non-null  object
 3   View              48288 non-null  object
 4   zenodo_name       49359 non-null  object
 5   zenodo_link       49359 non-null  object
 6   Sequence          48424 non-null  object
 7   Taxonomic_Name    45473 non-null  object
 8   Locality          34015 non-null  object
 9   Sample_accession  5884 non-null   object
 10  Collected_by      5280 non-null   object
 11  Other_ID          14382 non-null  object
 12  Date              33718 non-null  object
 13  Dataset           40405 non-null  object
 14  Store             39485 non-null  object
 15  Brood             14942 non-null  object
 16  Death_Date        318 non-null    object
 17  Cross_Type  

Observe that not all images have a species label.

In [27]:
df.loc[df.species.isna()].sample(7)

CAMID      X       Image_name     View  \
48538        E24  37559        E24_d.CR2   dorsal   
37246  CAM042045  43973  CAM042045_v.JPG  ventral   
37484  CAM042166  44211  CAM042166_v.JPG  ventral   
48780        E83  37777        E83_v.CR2  ventral   
3118     19N2627  22498    19N2627_v.CR2      NaN   
46111  CAM045060  42806  CAM045060_v.CR2  ventral   
39502  CAM043576  31097  CAM043576_v.CR2  ventral   

                              zenodo_name                        zenodo_link  \
48538  Anniina.Matilla.Field.Caught.E.csv  https://zenodo.org/record/2554218   
37246           Collection_August2019.csv  https://zenodo.org/record/5731587   
37484           Collection_August2019.csv  https://zenodo.org/record/5731587   
48780  Anniina.Matilla.Field.Caught.E.csv  https://zenodo.org/record/2554218   
3118   0.sheffield.ps.nn.ikiam.batch2.csv  https://zenodo.org/record/4288311   
46111   image.names.cook.island.erato.csv  https://zenodo.org/record/5526257   
39502  batch2.Peru.image.names.Zenodo.csv  https://zenodo.org/record/4287444   

      Sequence Taxonomic_Name Locality Sample_accession  ... Death_Date  \
48538      NaN            NaN      NaN              NaN  ...        NaN   
37246   42,045            NaN      NaN              NaN  ...        NaN   
37484   42,166            NaN      NaN              NaN  ...        NaN   
48780      NaN            NaN      NaN              NaN  ...        NaN   
3118         0            NaN      NaN              NaN  ...        NaN   
46111   45,060            NaN      NaN              NaN  ...        NaN   
39502   43,576            NaN      NaN              NaN  ...        NaN   

      Cross_Type Stage  Sex Unit_Type file_type record_number species  \
48538        NaN   NaN  NaN       NaN       raw       2554218     NaN   
37246        NaN   NaN  NaN       NaN       jpg       5731587     NaN   
37484        NaN   NaN  NaN       NaN       jpg       5731587     NaN   
48780        NaN   NaN  NaN       NaN       raw       2554218     NaN   
3118         NaN   NaN  NaN       NaN       raw       4288311     NaN   
46111        NaN   NaN  NaN       NaN       raw       5526257     NaN   
39502        NaN   NaN  NaN       NaN       raw       4287444     NaN   

      subspecies genus  
48538       None   NaN  
37246       None   NaN  
37484       None   NaN  
48780       None   NaN  
3118        None   NaN  
46111       None   NaN  
39502       None   NaN  

[7 rows x 26 columns]

### Update Master File with Genus through Subspecies Columns

In [28]:
df.to_csv("../Jiggins_Zenodo_Img_Master.csv", index = False)

### Make Heliconius Subset

In [29]:
heliconius_subset = df.loc[df.genus.str.lower() == "heliconius"]

heliconius_subset.info()

<class 'pandas.core.frame.DataFrame'>
Index: 34929 entries, 6 to 49358
Data columns (total 26 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             34929 non-null  object
 1   X                 34929 non-null  int64 
 2   Image_name        34929 non-null  object
 3   View              34150 non-null  object
 4   zenodo_name       34929 non-null  object
 5   zenodo_link       34929 non-null  object
 6   Sequence          34929 non-null  object
 7   Taxonomic_Name    34929 non-null  object
 8   Locality          23417 non-null  object
 9   Sample_accession  5860 non-null   object
 10  Collected_by      5280 non-null   object
 11  Other_ID          6404 non-null   object
 12  Date              23162 non-null  object
 13  Dataset           32846 non-null  object
 14  Store             29446 non-null  object
 15  Brood             14921 non-null  object
 16  Death_Date        316 non-null    object
 17  Cross_Type       

In [30]:
heliconius_subset.nunique()

CAMID                9546
X                   34929
Image_name          26946
View                    3
zenodo_name            31
zenodo_link            28
Sequence             8701
Taxonomic_Name        129
Locality              472
Sample_accession     1559
Collected_by           12
Other_ID             1865
Date                  776
Dataset                 8
Store                 121
Brood                 224
Death_Date             81
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               4
file_type               3
record_number          28
species                37
subspecies            110
genus                   1
dtype: int64

In [31]:
heliconius_subset.View.value_counts()

View
dorsal                17218
ventral               16914
dorsal and ventral       18
Name: count, dtype: int64

Note that this subset is distributed across 28 Zenodo records from the [Butterfly Genetics Group](https://zenodo.org/communities/butterfly?q=&l=list&p=1&s=10&sort=newest).

### Save the Heliconius Subset to CSV
We'll drop the `genus` column, since they're all `Heliconius`.

In [32]:
heliconius_subset[list(heliconius_subset.columns)[:-1]].to_csv("../Jiggins_Heliconius_Master.csv", index = False)